This is an example of using the API of [pymininec](https://pypi.org/project/pymininec/) together with the API of [plot-antenna](https://pypi.org/project/plot-antenna/). So we're computing an antenna with [pymininec](https://pypi.org/project/pymininec/) and then we display the antenna pattern, voltage standing wave ratio (VSWR), and antenna geometry using [plot-antenna](https://pypi.org/project/pymininec/). There is already a small [API description for plot-antenna](https://github.com/schlatterbeck/plot-antenna#plot-antenna-api), for pymininec we use the [main() function in mininec/mininec.py](https://github.com/schlatterbeck/pymininec/blob/master/mininec/mininec.py) &ndash; which contains calls to the mininec API as an example. Note that the API uses features of the currently not-yet-released version of pymininec from github.

In [1]:
import numpy as np
from copy import deepcopy
from mininec.mininec import *
from plot_antenna.plot_antenna import Gain_Data, Gain_Plot, Impedance_Data, process_args
from plot_antenna.plot_antenna import options_general, options_gain, options_swr, options_geo
from plot_antenna.plot_antenna import Loaded_Segment
from plotly_fix_fn import setup_plotly
setup_plotly ('content/2025/07/plotly', '28-en')
show_opt = dict (include_plotlyjs = 'directory')
show_opt = {}

geo = Geo_Container ()
r = 0.00238
feedtag = 2
# Add wires for a 12-element Yagi/Uda, lengths in meter
#                 nseg X1       Y1      Z1  X2       Y2      Z2 radius tag
geo.append (Wire (22, -0.51943, 0.00000, 0, 0.51943, 0.00000, 0, r,  1))
geo.append (Wire (22, -0.50165, 0.22331, 0, 0.50165, 0.22331, 0, r,  feedtag))
geo.append (Wire (22, -0.46991, 0.34215, 0, 0.46991, 0.34215, 0, r,  3))
geo.append (Wire (22, -0.46136, 0.64461, 0, 0.46136, 0.64461, 0, r,  4))
geo.append (Wire (22, -0.46224, 1.03434, 0, 0.46224, 1.03434, 0, r,  5))
geo.append (Wire (22, -0.45989, 1.55909, 0, 0.45989, 1.55909, 0, r,  6))
geo.append (Wire (22, -0.44704, 2.19682, 0, 0.44704, 2.19682, 0, r,  7))
geo.append (Wire (22, -0.43561, 2.94640, 0, 0.43561, 2.94640, 0, r,  8))
geo.append (Wire (22, -0.42672, 3.72364, 0, 0.42672, 3.72364, 0, r,  9))
geo.append (Wire (22, -0.41783, 4.53136, 0, 0.41783, 4.53136, 0, r, 10))
geo.append (Wire (22, -0.40894, 5.33400, 0, 0.40894, 5.33400, 0, r, 11))
geo.append (Wire (22, -0.39624, 6.04520, 0, 0.39624, 6.04520, 0, r, 12))
geo.compute_tags ()

# main mininec object, no ground (media)
m = Mininec (140, geo, media = None)

# Feedpoint at second wire (tag 2) pulse 11 (middle)
# pulses in API are 0-based!
feed = Excitation (cvolt = 1.0, geo_tag = feedtag, geo_idx = 10)
m.register_source (feed, pulse = 10, geo_tag = feedtag)
# Pattern
#         start, step, n
phi   = Angle (0, 5, 73) # from 0° to 360° in steps of 5°
theta = Angle (0, 5, 37) # from 0° to 180° in steps of 5°
# Now compute for frequencies 140 to 150 MHz in steps of 2 MHz
ff = {} # far field
idata = {} # Impedance data by frequency
for f in np.arange (140, 151, 2):
    m.f = f
    m.compute ()
    m.compute_far_field (theta, phi)
    key = (f, 'sum')
    # This gain_dbi is vertical, horizontal, total
    total = m.far_field.gain_dbi [-1].T
    ff [key] = Gain_Data.from_gains (key, total, theta.angle_deg (), phi.angle_deg ())
    idata [f] = Impedance_Data (f, feed.impedance)

In [2]:
# Now plot the far field using plot-antenna
cmd = options_general ()
options_gain (cmd)
options_swr (cmd)
options_geo (cmd)
args = process_args (cmd, [])
args.filename = ''
args.title = '12 element Yagi/Uda'
args.plot3d  = True
args.show_in_browser = True
# We need to copy ff if we want to reuse it later in another Gain_Plot object
# But we can usually get away modifying args later
gp = Gain_Plot (args, deepcopy (ff))
# Inject impedance data
gp.idata = idata
gp.compute ()
gp.plot (show_opt = show_opt)

In [3]:
# Plot elevation
args.plot3d = False
args.elevation = True
# We can re-use the same Gain_Plot object from before
#gp = Gain_Plot (args, deepcopy (ff))
#gp.compute ()
gp.plot (show_opt = show_opt)

In [4]:
# we could plot all diagrams in one go, it's enough to set args after gp.compute()
# Plot azimuth
args.plot3d = False
args.elevation = False
args.azimuth = True
gp.plot (show_opt = show_opt)

In [5]:
# Plot VSWR
args.plot3d = False
args.elevation = False
args.azimuth = False
args.plot_vswr = True
args.swr_show_bands = True
args.swr_show_impedance = True
gp.plot (show_opt = show_opt)

In [6]:
# Plot Geometry
pgeo = gp.new_geo (gnd = False)
for geobj in m.geo:
    pgeo.wires.append ([list (x) for x in geobj.endpoints])
    pgeo.append ([])
    for n, p in enumerate (geobj.pulse_iter ()):
        if n == 0:
            pgeo [-1].append (list (p.ends [0]))
        pgeo [-1].append (list (p.ends [1]))
pgeo.fix_wires ()
seg = list (m.pulses [feed.idx].point)
Loaded_Segment (gp.loaded_segs, seg, 'Excitation')
args.plot3d = False
args.elevation = False
args.azimuth = False
args.plot_vswr = False
args.plot_geo = True
gp.plot (show_opt = show_opt)